In [52]:
import folium
from folium import plugins
from folium.plugins import MarkerCluster
import psycopg2
import csv
import pandas as pd
import json
from area import area

from psycopg2.extensions import ISOLATION_LEVEL_AUTOCOMMIT 
from IPython.display import display

Data Clearning and Preparation

In [732]:
###connect to the postgres database

conn = psycopg2.connect(
    host = "127.0.0.1",
    database = "cbiproject_postgres",
    user = "postgres",
    password = "Cuihua2020@",
    port = "5432")

cur=conn.cursor()

<div class="alert alert-info">

  
    
## Requirement 1:

- The business intelligence reports are geared toward tracking and forecasting events that have direct or indirect impacts on businesses and neighborhoods in different zip codes within the city of Chicago. The business intelligence reports will be used to send alerts to taxi drivers about the state of COVID-19 in the different zip codes in order to avoid taxi drivers to be the super spreaders in the different zip codes and neighborhoods. For this report, we will use taxi trips and daily COVID-19 datasets for the city of Chicago.

</div>


In [57]:
#Requrement 1
query_taxi = ("SELECT * FROM taxi_trip")
cur.execute(query_taxi)
df_taxi = pd.DataFrame(cur.fetchall(), columns=['trip_id', 'start', 'end', 'pick_lat', 'pick_long', 'drop_lat', 'drop_long'])
df_taxi.info()


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4224091 entries, 0 to 4224090
Data columns (total 7 columns):
 #   Column     Dtype 
---  ------     ----- 
 0   trip_id    object
 1   start      object
 2   end        object
 3   pick_lat   object
 4   pick_long  object
 5   drop_lat   object
 6   drop_long  object
dtypes: object(7)
memory usage: 225.6+ MB


In [61]:
df_taxi = pd.concat([df_taxi, df_t['Taxi ID']], axis=1)

In [210]:
df_taxi1 = df_taxi.copy()

df_taxi1 = df_taxi1.dropna(subset=['pick_lat', 'drop_lat'], how='any')
df_taxi1['start'] = pd.to_datetime(df_taxi1['start'], errors='coerce', format='%Y-%m-%d %H:%M:%S')
df_taxi1['end'] = pd.to_datetime(df_taxi1['end'], errors='coerce', format='%Y-%m-%d %H:%M:%S')
df_taxi1['pick_lat'] = pd.to_numeric(df_taxi1['pick_lat'],errors='coerce')
df_taxi1['pick_long'] = pd.to_numeric(df_taxi1['pick_long'],errors='coerce')
df_taxi1['drop_lat'] = pd.to_numeric(df_taxi1['drop_lat'],errors='coerce')
df_taxi1['drop_long'] = pd.to_numeric(df_taxi1['drop_long'],errors='coerce')

df_taxi1.info()


<class 'pandas.core.frame.DataFrame'>
Int64Index: 3559628 entries, 0 to 4224090
Data columns (total 8 columns):
 #   Column     Dtype         
---  ------     -----         
 0   trip_id    object        
 1   start      datetime64[ns]
 2   end        datetime64[ns]
 3   pick_lat   float64       
 4   pick_long  float64       
 5   drop_lat   float64       
 6   drop_long  float64       
 7   Taxi ID    object        
dtypes: datetime64[ns](2), float64(4), object(2)
memory usage: 244.4+ MB


In [211]:
df_alert = df_taxi1.dropna(subset=['Taxi ID', 'pick_lat', 'pick_long'])
df_alert = df_alert[['trip_id','Taxi ID', 'start', 'end', 'pick_lat', 'pick_long', 'drop_lat', 'drop_long']].head(50000)
df_alert.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 50000 entries, 0 to 61452
Data columns (total 8 columns):
 #   Column     Non-Null Count  Dtype         
---  ------     --------------  -----         
 0   trip_id    50000 non-null  object        
 1   Taxi ID    50000 non-null  object        
 2   start      684 non-null    datetime64[ns]
 3   end        684 non-null    datetime64[ns]
 4   pick_lat   50000 non-null  float64       
 5   pick_long  50000 non-null  float64       
 6   drop_lat   50000 non-null  float64       
 7   drop_long  50000 non-null  float64       
dtypes: datetime64[ns](2), float64(4), object(2)
memory usage: 3.4+ MB


In [213]:
from uszipcode import SearchEngine, SimpleZipcode, Zipcode

search = SearchEngine() #initiate the engine


#mapping the corordinates 
for i, row in df_alert.iterrows():
    
    results_pick = search.by_coordinates(row['pick_lat'], row['pick_long'], radius = 5)
    df_alert.loc[i, 'pick_zip_code'] = results_pick[0].zipcode
    
    results_drop = search.by_coordinates(row['drop_lat'], row['drop_long'], radius = 5)
    df_alert.loc[i, 'drop_zip_code'] = results_drop[0].zipcode

In [215]:
##we can see the taxi trips have been mapped to zip code for both pick location and drop location
df_alert.head()

trip_id  \
0  af4a062154de887c0361b92249c626ee3cc11a8a   
1  9b0da45a8659d98c4be4d5d42ba9a93b935ae4ef   
2  92e4b609319e89f741ef90775536c2deeea6bfa5   
3  d581ab63b9c31f3c54d9504fce92af060f6286bc   
4  1d2f1b37d10b1ada9994bc7be9af2de75a318b17   

                                             Taxi ID      start  \
0  7e179f8ef66ae99ec2d1ec89224e0b7ee5469fe5627f6d... 2021-11-01   
1  2c508057a94474215bdea7b101edad0dc911ef61bb99e6... 2021-11-01   
2  31261f6e7fc645eff98c7964c7ea71a0ea7e387a6bd7f8... 2021-11-01   
3  f6138aa35e1fb074eb79fbe29f512b6153dca3593d8cd2... 2021-11-01   
4  2c508057a94474215bdea7b101edad0dc911ef61bb99e6... 2021-11-01   

                  end   pick_lat  pick_long   drop_lat  drop_long  \
0 2021-11-01 00:15:00  41.980264 -87.913625  41.922686 -87.649489   
1 2021-11-01 00:00:00  41.985015 -87.804532  41.978830 -87.771167   
2 2021-11-01 00:00:00  41.901207 -87.676356  41.922686 -87.649489   
3 2021-11-01 00:15:00  41.980264 -87.913625  41.901207 -87.676356   
4 2021-11-01 01:00:00  41.874005 -87.663518  42.009623 -87.670167   

  pick_zip_code drop_zip_code  
0         60018         60614  
1         60631         60630  
2         60622         60614  
3         60018         60622  
4         60607         60626

In [295]:
##now moving to covid data
query_covid = ("SELECT * FROM covid_zip")
cur.execute(query_covid)
df_covid = pd.DataFrame(cur.fetchall(), columns=["week_start", "zip_code_location", "cases_weekly", "deaths_weekly"])
df_covid.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5460 entries, 0 to 5459
Data columns (total 4 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   week_start         5460 non-null   object
 1   zip_code_location  5369 non-null   object
 2   cases_weekly       5237 non-null   object
 3   deaths_weekly      5460 non-null   object
dtypes: object(4)
memory usage: 170.8+ KB


In [302]:
df_covid_t = df_covid.dropna(subset =['zip_code_location'])
df_covid_t.describe()

week_start  \
count                      5369   
unique                       91   
top     2021-03-21T00:00:00.000   
freq                         59   

                                        zip_code_location cases_weekly  \
count                                                5369         5150   
unique                                                 59          395   
top     {'type': 'Point', 'coordinates': [-87.629531, ...            0   
freq                                                   91          131   

       deaths_weekly  
count           5369  
unique            23  
top                0  
freq            3037

In [311]:
import re

for i, row in df_covid_t.iterrows():
    m = row['zip_code_location']
    n = m[m.find("[")+1:m.find("]")]
    df_covid_t.loc[i,'long'] = n[:n.find(",")]
    df_covid_t.loc[i,'lat'] = n[n.find(",")+2:]
    
df_covid_t['lat'] = pd.to_numeric(df_covid_t['lat'],errors='coerce')
df_covid_t['long'] = pd.to_numeric(df_covid_t['long'],errors='coerce')
    

/Users/shawn_liu/opt/anaconda3/lib/python3.8/site-packages/pandas/core/indexing.py:670: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  iloc._setitem_with_indexer(indexer, value)
<ipython-input-311-ddf72bfd200e>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_covid_t.loc[i,'long'] = n[:n.find(",")]
<ipython-input-311-ddf72bfd200e>:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_covid_t.loc[i,'lat'] = n[n.find(",")+2:]
<ipython-in

In [313]:
#now need to map the coordinates to zip code
for i, row in df_covid_t.iterrows():
    
    results = search.by_coordinates(row['lat'], row['long'], radius=5)
    df_covid_t.loc[i, 'zip_code'] = results[0].zipcode
    
df_covid_t.head()

week_start                                  zip_code_location  \
0  2021-11-21T00:00:00.000  {'type': 'Point', 'coordinates': [-87.622844, ...   
1  2021-03-21T00:00:00.000  {'type': 'Point', 'coordinates': [-87.63676, 4...   
2  2021-03-28T00:00:00.000  {'type': 'Point', 'coordinates': [-87.63676, 4...   
3  2021-09-12T00:00:00.000  {'type': 'Point', 'coordinates': [-87.670366, ...   
4  2021-10-17T00:00:00.000  {'type': 'Point', 'coordinates': [-87.670366, ...   

  cases_weekly deaths_weekly        lat       long zip_code  
0           18             0  41.886262 -87.622844    60602  
1            8             0  41.882634 -87.636760    60606  
2            3             0  41.882634 -87.636760    60606  
3           55             2  41.849879 -87.670366    60608  
4           60             1  41.849879 -87.670366    60608

In [323]:
#then we will need to select most recent covid information to distribute to the taxi drivers

df_covid_new = df_covid_t.sort_values('week_start').groupby('zip_code').tail(1)
df_covid_new['zip_code'].nunique()

57

In [378]:
#we can compile the information message to send to taxi driver based on the zip code he/she pick up / drop passengers

test = df_alert.sample()
test_zip = test['pick_zip_code'].values[0]
test_case = df_covid_new['cases_weekly'][df_covid_new['zip_code'] == test_zip].values[0]
test_death = df_covid_new['deaths_weekly'][df_covid_new['zip_code'] == test_zip].values[0]

print('Hello! The community {0} currently has {1} covid cases and {2} deaths'.format(test_zip, test_case, test_death))

Hello! The community 60618 currently has 119 covid cases and 0 deaths


<div class="alert alert-info">

  
    
## Requirement 2:

- There are two major airports within the city of Chicago: Ohare and Midway. And we are interested to track trips from these airports to the different zip codes and the reported COVID-19 positive test cases. The city of Chicago is interested to monitor the traffic of the taxi trips from these airports to the different neighborhoods and zip codes

</div>


In [379]:
#used coordinates of Ohare and Midway Airports to filter down the trips from the two airports to different neighborhood

import math

lat_Ohare = 41.978611
long_Ohare = -87.904724

lat_Midway = 41.786775
long_Midway = -87.752188

df_pick_ohare = pd.DataFrame(columns=['trip_id', 'Taxi ID', 'start', 'end', 'pick_lat', 'pick_long'])
for i, row in df_alert.iterrows():
    if math.isclose(row['pick_lat'], lat_Ohare, rel_tol=0.01) and math.isclose(row['pick_long'], long_Ohare, rel_tol=0.01):
        df_pick_ohare = df_pick_ohare.append(df_alert.loc[i])

In [380]:
df_pick_ohare.head()

trip_id  \
0  af4a062154de887c0361b92249c626ee3cc11a8a   
1  9b0da45a8659d98c4be4d5d42ba9a93b935ae4ef   
2  92e4b609319e89f741ef90775536c2deeea6bfa5   
3  d581ab63b9c31f3c54d9504fce92af060f6286bc   
4  1d2f1b37d10b1ada9994bc7be9af2de75a318b17   

                                             Taxi ID      start  \
0  7e179f8ef66ae99ec2d1ec89224e0b7ee5469fe5627f6d... 2021-11-01   
1  2c508057a94474215bdea7b101edad0dc911ef61bb99e6... 2021-11-01   
2  31261f6e7fc645eff98c7964c7ea71a0ea7e387a6bd7f8... 2021-11-01   
3  f6138aa35e1fb074eb79fbe29f512b6153dca3593d8cd2... 2021-11-01   
4  2c508057a94474215bdea7b101edad0dc911ef61bb99e6... 2021-11-01   

                  end   pick_lat  pick_long   drop_lat  drop_long  \
0 2021-11-01 00:15:00  41.980264 -87.913625  41.922686 -87.649489   
1 2021-11-01 00:00:00  41.985015 -87.804532  41.978830 -87.771167   
2 2021-11-01 00:00:00  41.901207 -87.676356  41.922686 -87.649489   
3 2021-11-01 00:15:00  41.980264 -87.913625  41.901207 -87.676356   
4 2021-11-01 01:00:00  41.874005 -87.663518  42.009623 -87.670167   

  drop_zip_code pick_zip_code  
0         60614         60018  
1         60630         60631  
2         60614         60622  
3         60622         60018  
4         60626         60607

In [382]:
df_pick_midway = pd.DataFrame()
for i, row in df_alert.iterrows():
    if math.isclose(row['pick_lat'], lat_Midway, rel_tol=0.01) and math.isclose(row['pick_long'], long_Midway, rel_tol=0.01):
        df_pick_midway = df_pick_midway.append(df_alert.loc[i])

In [388]:
from datetime import datetime

df_pick_ohare['start_date'] = df_pick_ohare['start'].dt.date
df_pick_midway['start_date'] = df_pick_midway['start'].dt.date

In [395]:
df_traffic_ohare = df_pick_ohare.groupby(['drop_zip_code', 'start_date']).size()
df_traffic_midway = df_pick_midway.groupby(['drop_zip_code', 'start_date']).size()

drop_zip_code  start_date
60018          2021-10-31    35
60176          2021-10-31     7
60601          2021-10-31    18
60602          2021-10-31    14
60603          2021-10-31     8
dtype: int64

<div class="alert alert-info">

  
    
## Requirement 3:

- The city of Chicago has created the COVID-19 Community Vulnerability Index (CCVI) (https://data.cityofchicago.org/Health-Human-
     
Services/Chicago-COVID-19-Community-Vulnerability-Index-CCV/xhc6- 88s9 ) to identify communities that have been disproportionately affected by COVID-19 and are vulnerable to barriers to COVID-19 vaccine uptake. The city of Chicago is interested to track the number of taxi trips from/to the neighborhoods that have CCVI Category with value HIGH

</div>



In [449]:
query_ccvi = ("SELECT * FROM ccvi WHERE ccvi_category = 'HIGH'")
try:
    cur.execute(query_ccvi)
except:
    cur.rollback()
df_ccvi = pd.DataFrame(cur.fetchall(), columns=["ccvi_category", "community_area_or_zip", "location"])
df_ccvi.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 39 entries, 0 to 38
Data columns (total 3 columns):
 #   Column                 Non-Null Count  Dtype 
---  ------                 --------------  ----- 
 0   ccvi_category          39 non-null     object
 1   community_area_or_zip  39 non-null     object
 2   location               39 non-null     object
dtypes: object(3)
memory usage: 1.0+ KB


In [450]:
df_ccvi.head()

ccvi_category community_area_or_zip  \
0          HIGH                    57   
1          HIGH                    25   
2          HIGH                    53   
3          HIGH                 60636   
4          HIGH                    47   

                                            location  
0  {'type': 'Point', 'coordinates': [-87.72636332...  
1  {'type': 'Point', 'coordinates': [-87.75604671...  
2  {'type': 'Point', 'coordinates': [-87.63573977...  
3  {'type': 'Point', 'coordinates': [-87.668597, ...  
4  {'type': 'Point', 'coordinates': [-87.59647559...

In [483]:
#extract latitude and longitude from location field

import re

for i, row in df_ccvi.iterrows():
    m = row['location']
    n = m[m.find("[")+1:m.find("]")]
    df_ccvi.loc[i,'long'] = n[:n.find(",")]
    df_ccvi.loc[i,'lat'] = n[n.find(",")+2:]
    
df_ccvi['lat'] = pd.to_numeric(df_ccvi['lat'],errors='coerce')
df_ccvi['long'] = pd.to_numeric(df_ccvi['long'],errors='coerce')


for i, row in df_ccvi.iterrows():
    
    results = search.by_coordinates(row['lat'], row['long'], radius=5)
    df_ccvi.loc[i, 'zip_code'] = results[0].zipcode
    
df_ccvi.head()

ccvi_category community_area_or_zip  \
0          HIGH                    57   
1          HIGH                    25   
2          HIGH                    53   
3          HIGH                 60636   
4          HIGH                    47   

                                            location       long        lat  \
0  {'type': 'Point', 'coordinates': [-87.72636332... -87.726363  41.810879   
1  {'type': 'Point', 'coordinates': [-87.75604671... -87.756047  41.890609   
2  {'type': 'Point', 'coordinates': [-87.63573977... -87.635740  41.673820   
3  {'type': 'Point', 'coordinates': [-87.668597, ... -87.668597  41.775990   
4  {'type': 'Point', 'coordinates': [-87.59647559... -87.596476  41.728182   

  zip_code  
0    60632  
1    60644  
2    60628  
3    60636  
4    60619

In [452]:
import json
import os
from collections import namedtuple
import sys
from math import log,tan,pi,radians

In [453]:
#set up global variables
Pt = namedtuple('Pt','x,y')
Edge = namedtuple('Edge','a,b')
Poly = namedtuple('Poly','name,edges')
_eps = 1e-5
_huge = sys.float_info.max
_tiny = sys.float_info.min

In [454]:
def load_json():
    file_in = open("/Users/shawn_liu/Desktop/MSDS/Data Engineering_MSDS432/Chicago Business Intelligecne report/Neighborhoods_2012_polygons.json")
    d = json.load(file_in)
    return d

In [456]:
def spherical_mercator_projection(longitude,latitude):
    #http://en.wikipedia.org/wiki/Mercator_projection <- invented in 1569!
    #http://stackoverflow.com/questions/4287780/detecting-whether-a-gps-coordinate-falls-within-a-polygon-on-a-map
    x = -longitude
    y = log(tan(radians(pi/4 + latitude/2)))
    return (x,y)

In [457]:
def rayintersectseg(p, edge):
    #http://rosettacode.org/wiki/Ray-casting_algorithm#Python
    #takes a point p=Pt() and an edge of two endpoints a,b=Pt() of a line segment returns boolean
    a,b = edge
    if a.y > b.y:
        a,b = b,a
    if p.y == a.y or p.y == b.y:
        p = Pt(p.x, p.y + _eps)
    intersect = False
 
    if (p.y > b.y or p.y < a.y) or (
        p.x > max(a.x, b.x)):
        return False
 
    if p.x < min(a.x, b.x):
        intersect = True
    else:
        if abs(a.x - b.x) > _tiny:
            m_red = (b.y - a.y) / float(b.x - a.x)
        else:
            m_red = _huge
        if abs(a.x - p.x) > _tiny:
            m_blue = (p.y - a.y) / float(p.x - a.x)
        else:
            m_blue = _huge
        
        intersect = m_blue >= m_red
    return intersect

In [458]:
def is_odd(x): 
    return x%2 == 1

def ispointinside(p, poly):
    ln = len(poly)
    return is_odd(sum(rayintersectseg(p, edge)
                    for edge in poly.edges ))


In [459]:
def get_all_neighborhoods():
    d = load_json()
    shape_list=[]
    for shape_idx in range(len(d['features'])):
        name = d['features'][shape_idx]['properties']['SEC_NEIGH']

        edges =[]
        for coordinate_idx in range(len(d['features'][shape_idx]['geometry']['coordinates'][0])-1):
            lon_1 = d['features'][shape_idx]['geometry']['coordinates'][0][coordinate_idx][0]
            lat_1 = d['features'][shape_idx]['geometry']['coordinates'][0][coordinate_idx][1]

            lon_2 = d['features'][shape_idx]['geometry']['coordinates'][0][coordinate_idx+1][0]
            lat_2 = d['features'][shape_idx]['geometry']['coordinates'][0][coordinate_idx+1][1]

            x1,y1 = spherical_mercator_projection(lon_1,lat_1)
            x2,y2 = spherical_mercator_projection(lon_2,lat_2)
            edges.append(Edge(a=Pt(x=x1,y=y1),b=Pt(x=x2,y=y2)))

        shape_list.append(Poly(name=name,edges=tuple(edges)))
    return shape_list

In [461]:
def find_neighborhood(test_long,test_lat,all_neighborhoods):
    x,y = spherical_mercator_projection(test_long,test_lat)
    for neighborhood in all_neighborhoods:
        correct_neighborhood = ispointinside(Pt(x=x,y=y),neighborhood)
        if correct_neighborhood:
            return neighborhood.name

In [463]:
all_neighborhoods = get_all_neighborhoods()

[Poly(name='BRONZEVILLE', edges=(Edge(a=Pt(x=87.60670812560363, y=-0.9217478630076589), b=Pt(x=87.60670480953505, y=-0.9217538258306156)), Edge(a=Pt(x=87.60670480953505, y=-0.9217538258306156), b=Pt(x=87.60670022648407, y=-0.9217599331675534)), Edge(a=Pt(x=87.60670022648407, y=-0.9217599331675534), b=Pt(x=87.60669581538588, y=-0.9217660147054346)), Edge(a=Pt(x=87.60669581538588, y=-0.9217660147054346), b=Pt(x=87.60668982110376, y=-0.9217733209271359)), Edge(a=Pt(x=87.60668982110376, y=-0.9217733209271359), b=Pt(x=87.60668357216157, y=-0.9217795583116337)), Edge(a=Pt(x=87.60668357216157, y=-0.9217795583116337), b=Pt(x=87.60667660553894, y=-0.9217863271632843)), Edge(a=Pt(x=87.60667660553894, y=-0.9217863271632843), b=Pt(x=87.6066796364493, y=-0.9217940956428113)), Edge(a=Pt(x=87.6066796364493, y=-0.9217940956428113), b=Pt(x=87.60668235893172, y=-0.9218010736791348)), Edge(a=Pt(x=87.60668235893172, y=-0.9218010736791348), b=Pt(x=87.60667153481008, y=-0.9218121999059804)), Edge(a=Pt(x=87.

In [464]:
test_long = -87.624069
test_lat = 41.862889

neighborhood = find_neighborhood(test_long,test_lat,all_neighborhoods)
print(neighborhood)

NEAR SOUTH SIDE


In [569]:
df_from = df_alert[['trip_id', 'pick_lat', 'pick_long']]
df_to = df_alert[['trip_id', 'drop_lat', 'drop_long']]

In [570]:
def nbr(df, long, lat):
    for i, row in df.iterrows():
        df.loc[i, 'neighbor'] = find_neighborhood(row[long], row[lat], all_neighborhoods)


In [571]:
nbr(df_from, 'pick_long', 'pick_lat')

/Users/shawn_liu/opt/anaconda3/lib/python3.8/site-packages/pandas/core/indexing.py:1596: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.obj[key] = _infer_fill_value(value)
/Users/shawn_liu/opt/anaconda3/lib/python3.8/site-packages/pandas/core/indexing.py:1765: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  isetter(loc, value)


In [572]:
nbr(df_to, 'drop_long', 'drop_lat')

In [573]:
trip_from_df = df_from.groupby(['neighbor'])['trip_id'].count().reset_index(name = 'number of trips')
trip_to_df = df_to.groupby(['neighbor'])['trip_id'].count().reset_index(name = 'number of trips')

In [574]:
##map ccvi location (lat, long) to neighborhood name
nbr(df_ccvi, 'long', 'lat')

In [581]:
df_pi = df_ccvi.merge(trip_from_df, on='neighbor', how='left').rename(columns={'number of trips':'pick'})
df_con = df_pi.merge(trip_to_df, on='neighbor', how='left').rename(columns={'number of trips':'drop'})

In [587]:
df_con = df_con[['ccvi_category', 'zip_code', 'neighbor', 'pick', 'drop']]
df_con['total_traffic'] = df_con['pick'] + df_con['drop']
df_con

ccvi_category zip_code                     neighbor    pick    drop  \
0           HIGH    60632   ARCHER HEIGHTS,WEST ELSDON   183.0   182.0   
1           HIGH    60644                       AUSTIN  1111.0  1127.0   
2           HIGH    60628                 WEST PULLMAN   278.0   239.0   
3           HIGH    60636                    ENGLEWOOD   768.0   735.0   
4           HIGH    60619             CHATHAM,BURNSIDE   496.0   545.0   
5           HIGH    60632  BRIGHTON PARK,MCKINLEY PARK   442.0   398.0   
6           HIGH    60623               LITTLE VILLAGE   418.0   393.0   
7           HIGH    60629   ARCHER HEIGHTS,WEST ELSDON   183.0   182.0   
8           HIGH    60707                         None     NaN     NaN   
9           HIGH    60609            BACK OF THE YARDS   450.0   446.0   
10          HIGH    60609            BACK OF THE YARDS   450.0   446.0   
11          HIGH    60624               NORTH LAWNDALE   556.0   542.0   
12          HIGH    60620               AUBURN GRESHAM   529.0   509.0   
13          HIGH    60629     MARQUETTE PARK,GAGE PARK   637.0   581.0   
14          HIGH    60621                    ENGLEWOOD   768.0   735.0   
15          HIGH    60620               AUBURN GRESHAM   529.0   509.0   
16          HIGH    60629                    WEST LAWN   145.0   151.0   
17          HIGH    60707          MONTCLARE, GALEWOOD    95.0    81.0   
18          HIGH    60651                HUMBOLDT PARK   865.0   692.0   
19          HIGH    60644                       AUSTIN  1111.0  1127.0   
20          HIGH    60639       BELMONT CRAGIN,HERMOSA   564.0   567.0   
21          HIGH    60628  WASHINGTON HEIGHTS,ROSELAND   701.0   601.0   
22          HIGH    60636                    ENGLEWOOD   768.0   735.0   
23          HIGH    60651                HUMBOLDT PARK   865.0   692.0   
24          HIGH    60628  WASHINGTON HEIGHTS,ROSELAND   701.0   601.0   
25          HIGH    60639       BELMONT CRAGIN,HERMOSA   564.0   567.0   
26          HIGH    60633               SOUTHEAST SIDE   150.0   164.0   
27          HIGH    60621                    ENGLEWOOD   768.0   735.0   
28          HIGH    60643  WASHINGTON HEIGHTS,ROSELAND   701.0   601.0   
29          HIGH    60623               LITTLE VILLAGE   418.0   393.0   
30          HIGH    60629     MARQUETTE PARK,GAGE PARK   637.0   581.0   
31          HIGH    60624                GARFIELD PARK   660.0   620.0   
32          HIGH    60638               MIDWAY AIRPORT   509.0   596.0   
33          HIGH    60653            BACK OF THE YARDS   450.0   446.0   
34          HIGH    60608              LOWER WEST SIDE   620.0   575.0   
35          HIGH    60639      BELMONT CRAIGIN,HERMOSA   223.0   199.0   
36          HIGH    60632  BRIGHTON PARK,MCKINLEY PARK   442.0   398.0   
37          HIGH    60629     MARQUETTE PARK,GAGE PARK   637.0   581.0   
38          HIGH    60624                GARFIELD PARK   660.0   620.0   

    total_traffic  
0           365.0  
1          2238.0  
2           517.0  
3          1503.0  
4          1041.0  
5           840.0  
6           811.0  
7           365.0  
8             NaN  
9           896.0  
10          896.0  
11         1098.0  
12         1038.0  
13         1218.0  
14         1503.0  
15         1038.0  
16          296.0  
17          176.0  
18         1557.0  
19         2238.0  
20         1131.0  
21         1302.0  
22         1503.0  
23         1557.0  
24         1302.0  
25         1131.0  
26          314.0  
27         1503.0  
28         1302.0  
29          811.0  
30         1218.0  
31         1280.0  
32         1105.0  
33          896.0  
34         1195.0  
35          422.0  
36          840.0  
37         1218.0  
38         1280.0

<div class="alert alert-info">

  
    
## Requirement 4:

- For streetscaping investment and planning, the city of Chicago is interested to forecast daily, weekly, and monthly traffic patterns utilizing the taxi trips for the different zip codes.


</div>

In [631]:
#generate time series data from previous work

df_day_trip = df_t[['Trip ID','Trip Start Timestamp', 'Pickup Centroid Latitude', 'Pickup Centroid Longitude',
       'Dropoff Centroid Latitude','Dropoff Centroid Longitude']].rename(columns={'Trip Start Timestamp' : 'start', 'Pickup Centroid Latitude':'pick_lat', 'Pickup Centroid Longitude':'pick_long',
       'Dropoff Centroid Latitude':'drop_lat','Dropoff Centroid Longitude': 'drop_long'})
df_day_trip.head()


Trip ID                   start  \
0  02fc5d8c3e8525a49b7514bd6c2b3301c2d6aa79  01/01/2021 12:00:00 AM   
1  33eb5c7a1439ac1e3ec6d1520e21db8137d1d11b  01/01/2021 12:00:00 AM   
2  4bcfcfa78f372b705214ee2cba9c765ad6ba5161  01/01/2021 12:00:00 AM   
3  655bbd9bcb0a78ee003e304ebbe350b21cdd7083  01/01/2021 12:00:00 AM   
4  7b7b8108de94a518607068a7369ceea1ab2ae924  01/01/2021 12:00:00 AM   

    pick_lat  pick_long   drop_lat  drop_long  
0        NaN        NaN  41.975171 -87.687516  
1  41.792592 -87.769615        NaN        NaN  
2  41.899602 -87.633308  41.899602 -87.633308  
3  41.775929 -87.666596  41.775929 -87.666596  
4  41.836150 -87.648788  41.850266 -87.667569

In [623]:


df_day_trip = df_day_trip.dropna(subset=['pick_lat', 'drop_lat'], how='any')
df_day_trip['pick_lat'] = pd.to_numeric(df_day_trip['pick_lat'],errors='coerce')
df_day_trip['pick_long'] = pd.to_numeric(df_day_trip['pick_long'],errors='coerce')
df_day_trip['drop_lat'] = pd.to_numeric(df_day_trip['drop_lat'],errors='coerce')
df_day_trip['drop_long'] = pd.to_numeric(df_day_trip['drop_long'],errors='coerce')

df_day_trip.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 2623038 entries, 2 to 3072476
Data columns (total 6 columns):
 #   Column     Dtype  
---  ------     -----  
 0   Trip ID    object 
 1   start      object 
 2   pick_lat   float64
 3   pick_long  float64
 4   drop_lat   float64
 5   drop_long  float64
dtypes: float64(4), object(2)
memory usage: 140.1+ MB


In [640]:
df_day_trip['start_date'] = pd.to_datetime(df_day_trip['start'])
df_day_trip['start_date'] = df_day_trip['start_date'].dt.date
df_day_trip['start_date'].isnull().sum()

0

In [650]:
df_day_trip = df_day_trip.dropna()

In [766]:
##because the large dataset of taxi trip and computing time, I used stratified sampling by datetime to reduce the size

df_day_trip_s = df_day_trip.groupby('start_date').apply(lambda x: x.sample(frac=0.05))

In [767]:
from uszipcode import SearchEngine, SimpleZipcode, Zipcode

search = SearchEngine() #initiate the engine


#mapping the corordinates 
for i, row in df_day_trip_s.iterrows():
    
    results_pick = search.by_coordinates(row['pick_lat'], row['pick_long'], radius = 5)
    df_day_trip_s.loc[i, 'pick_zip_code'] = results_pick[0].zipcode

In [ ]:
df_to_zip = df_day_trip.groupby(['drop_zip_code', 'star_date']).size().reset_index(name = 'drops')
df_from_zip = df_day_trip.groupby(['pick_zip_code', 'star_date']).size().reset_index(name = 'picks')

In [ ]:
df_to_zip.rename(columns={'drop_zip_code' : 'zip'})
df_from_zip.rename(columns={'pick_zip_code' : 'zip'})

In [ ]:
df_traffic_21 = pd.merge(df_to_trip, df_from_trip, on='zip', how='outer')

df_traffic_21['traffic'] = df_traffic_21['drops'] + df_traffic_21['picks']
df_tra = df_traffic_21['zip','start_date', 'traffic']

df_tra['week'] =  df_tra['start_date'].dt.week
df_tra['month'] =  df_tra['start_date'].dt.month


### Daily Traffic Forecast -     
#### Forecasting orders for zip code: 60535

In [ ]:
df_tra_test = df_tra[df_tra['zip'] == 60535]
df_tra_daily = df_tra_test[['start' , 'traffic']]

In [ ]:
import pystan
import prophet
from prophet import Prophet
from prophet.diagnostics import cross_validation
from prophet.diagnostics import performance_metrics
from prophet.plot import plot_cross_validation_metric
from prophet.plot import plot_plotly, plot_components_plotly

In [ ]:
model = Prophet(yearly_seasonality=True, daily_seasonality=True)
model.fit(df_tra_daily) 
future_dates = model.make_future_dataframe(periods = 50, freq='W')
forecast = model.predict(future_dates)

model.plot(forecast)

In [ ]:
model.plot_components(forecast);

#### Weekly Traffic Forecast

In [ ]:
df_tra_week = df_tra_test.groupby('week')['traffic'].sum().reset_index(name = 'weekly_draffic')

In [ ]:
model = Prophet(yearly_seasonality=True, daily_seasonality=True)
model.fit(df_tra_daily) 
future_dates = model.make_future_dataframe(periods = 20, freq='W')
forecast = model.predict(future_dates)

model.plot(forecast)

#### Monthly Traffic Forecast

In [ ]:
df_tra_month = df_tra_test.groupby('month')['traffic'].sum().reset_index(name = 'monthly_draffic')

In [ ]:
model = Prophet(yearly_seasonality=True, daily_seasonality=True)
model.fit(df_tra_daily) 
future_dates = model.make_future_dataframe(periods = 6, freq='M')
forecast = model.predict(future_dates)

model.plot(forecast)

<div class="alert alert-info">

  
    
## Requirement 5:

- For industrial and neighborhood infrastructure investment, the city of Chicago is interested to invest in top 5 neighborhoods with highest unemployment rate and poverty rate and waive the fees for building permits in those neighborhoods in order to encourage businesses to develop and invest in those neighborhoods. Both, building permits and unemployment, datasets will be used in this report.


</div>


In [653]:
df_economy = pd.read_csv('/Users/shawn_liu/Desktop/MSDS/Data Engineering_MSDS432/Chicago Business Intelligecne report/economy.csv')
df_economy.head()

Community Area Community Area Name  Birth Rate  General Fertility Rate  \
0               1         Rogers Park        16.4                    62.0   
1               2          West Ridge        17.3                    83.3   
2               3              Uptown        13.1                    50.5   
3               4      Lincoln Square        17.1                    61.0   
4               5        North Center        22.4                    76.2   

   Low Birth Weight  Prenatal Care Beginning in First Trimester  \
0              11.0                                        73.0   
1               8.1                                        71.1   
2               8.3                                        77.7   
3               8.1                                        80.5   
4               9.1                                        80.4   

   Preterm Births  Teen Birth Rate  Assault (Homicide)  \
0            11.2             40.8                 7.7   
1             8.3             29.9                 5.8   
2            10.3             35.1                 5.4   
3             9.7             38.4                 5.0   
4             9.8              8.4                 1.0   

   Breast cancer in females  ...  Childhood Lead Poisoning  \
0                      23.3  ...                       0.5   
1                      20.2  ...                       1.0   
2                      21.3  ...                       0.5   
3                      21.7  ...                       0.4   
4                      16.6  ...                       0.9   

   Gonorrhea in Females  Gonorrhea in Males  Tuberculosis  \
0                 322.5               423.3          11.4   
1                 141.0               205.7           8.9   
2                 170.8               468.7          13.6   
3                  98.8               195.5           8.5   
4                  85.4               188.6           1.9   

   Below Poverty Level  Crowded Housing  Dependency  No High School Diploma  \
0                 22.7              7.9        28.8                    18.1   
1                 15.1              7.0        38.3                    19.6   
2                 22.7              4.6        22.2                    13.6   
3                  9.5              3.1        25.6                    12.5   
4                  7.1              0.2        25.5                     5.4   

   Per Capita Income  Unemployment  
0              23714           7.5  
1              21375           7.9  
2              32355           7.7  
3              35503           6.8  
4              51615           4.5  

[5 rows x 29 columns]

In [700]:
df_commu_5 = df_economy.sort_values(by=['Unemployment'])[:5]
inv_list = [int(x) for x in df_commu_5['Community Area'].tolist()]

In [701]:
inv_list

[32, 5, 7, 76, 6]

In [696]:
###fetch building permit

query_bldgpmt = 'SELECT id, community_area FROM bldgpmt'

try:
    cur.execute(query_bldgpmt)
except:
    cur.rollback()
df_bldgpmt = pd.DataFrame(cur.fetchall(), columns=['id', 'Community Area'])
df_bldgpmt.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 200000 entries, 0 to 199999
Data columns (total 2 columns):
 #   Column          Non-Null Count   Dtype 
---  ------          --------------   ----- 
 0   id              200000 non-null  object
 1   Community Area  98919 non-null   object
dtypes: object(2)
memory usage: 3.1+ MB


In [699]:
df_bldgpmt['Community Area'][9] == 58

True

In [702]:
df_bldgpmt = df_bldgpmt.dropna(subset=['Community Area'])
df_bldgpmt['Community Area'] = df_bldgpmt['Community Area'].astype(int)


In [703]:
df_bldgpmt_5 = df_bldgpmt[df_bldgpmt['Community Area'].isin(inv_list)]
df_bldgpmt_5.merge(df_commu_5, on='Community Area', how = 'left') 

id  Community Area Community Area Name  Birth Rate  \
0      2060019              76              O'Hare        15.8   
1      3053734               6           Lake View        13.5   
2      3137773               6           Lake View        13.5   
3      3060320               7        Lincoln Park        13.2   
4      3060308               7        Lincoln Park        13.2   
...        ...             ...                 ...         ...   
18175  2022069               5        North Center        22.4   
18176  2022077               5        North Center        22.4   
18177  2022108              32                Loop         9.4   
18178  2022143               6           Lake View        13.5   
18179  2022169              32                Loop         9.4   

       General Fertility Rate  Low Birth Weight  \
0                        70.0               3.5   
1                        38.7               6.3   
2                        38.7               6.3   
3                        38.7               6.6   
4                        38.7               6.6   
...                       ...               ...   
18175                    76.2               9.1   
18176                    76.2               9.1   
18177                    27.7               5.3   
18178                    38.7               6.3   
18179                    27.7               5.3   

       Prenatal Care Beginning in First Trimester  Preterm Births  \
0                                            82.0             5.0   
1                                            79.1             8.1   
2                                            79.1             8.1   
3                                            75.7             7.8   
4                                            75.7             7.8   
...                                           ...             ...   
18175                                        80.4             9.8   
18176                                        80.4             9.8   
18177                                        78.2             6.9   
18178                                        79.1             8.1   
18179                                        78.2             6.9   

       Teen Birth Rate  Assault (Homicide)  ...  Childhood Lead Poisoning  \
0                 15.9                 5.6  ...                       0.5   
1                 15.8                 1.4  ...                       0.4   
2                 15.8                 1.4  ...                       0.4   
3                  2.1                 0.7  ...                       0.6   
4                  2.1                 0.7  ...                       0.6   
...                ...                 ...  ...                       ...   
18175              8.4                 1.0  ...                       0.9   
18176              8.4                 1.0  ...                       0.9   
18177              1.3                 0.7  ...                       0.3   
18178             15.8                 1.4  ...                       0.4   
18179              1.3                 0.7  ...                       0.3   

       Gonorrhea in Females  Gonorrhea in Males  Tuberculosis  \
0                       NaN                   .           6.3   
1                      81.8               357.6           3.2   
2                      81.8               357.6           3.2   
3                      50.3                93.1           1.2   
4                      50.3                93.1           1.2   
...                     ...                 ...           ...   
18175                  85.4               188.6           1.9   
18176                  85.4               188.6           1.9   
18177                 129.9               200.5           6.5   
18178                  81.8               357.6           3.2   
18179                 129.9               200.5           6.5   

       Below Poverty Level  Crowded Housing  Dependency  \
0           

In [710]:
df_bldgpmt_5.groupby('Community Area').size()

Community Area
5     1852
6     3960
7     3636
32    7480
76    1252
dtype: int64

<div class="alert alert-info">

  
    
## Requirement 6:

- According to a report published by Crain’s Chicago Business (https://www.chicagobusiness.com/private-intelligence/industrial- market-crazy-right-now), The “little guys”, small businesses, have trouble competing with the big players like Amazon and Walmart for warehouse spaces. To help small business, a new program has been piloted with the name Illinois Small Business Emergency Loan Fund Delta to offer small businesses low interest loans of up to $250,000 for those applicants with PERMIT_TYPE of PERMIT - NEW CONSTRUCTION in the zip code that has the lowest number of PERMIT - NEW CONSTRUCTION applications and PER CAPITA INCOME is less than 30,000 for the planned construction site. Both, building permits and unemployment, datasets will be used in this report.to invest in top 5 neighborhoods with highest unemployment rate and poverty rate and waive the fees for building permits in those neighborhoods in order to encourage businesses to develop and invest in those neighborhoods. Both, building permits and unemployment, datasets will be used in this report.


</div>


In [739]:
query_bldg_new = "SELECT * FROM bldgpmt_full"

try:
    cur.execute(query_bldg_new)
except:
    conn.rollback()
df_bldgpmt_new = pd.DataFrame(cur.fetchall(), columns=['id', 'type','Community Area'])
df_bldgpmt_new = df_bldgpmt_new.dropna(subset = ['Community Area'])[1:]

In [743]:
df_bldgpmt_new1 = df_bldgpmt_new[df_bldgpmt_new['type'] == 'PERMIT - NEW CONSTRUCTION']

In [751]:
df_less_income = df_economy[df_economy['Per Capita Income'] <= 30000]

In [754]:
income_list = [int(x) for x in df_less_income['Community Area'].tolist()]

In [758]:
df_loan = df_bldgpmt_new1[df_bldgpmt_new1['Community Area'].astype(int).isin(income_list)]

In [760]:
df_loan_5 = df_loan.groupby(['Community Area']).size().reset_index(name = 'application number')
df_loan_5 = df_loan_5.sort_values(by=['application number'])

In [762]:
df_loan_5.head(5)

Community Area  application number
38             54                  28
31             47                  36
32             48                  52
29             45                  64
23             37                  68